In [2]:
!python --version
%matplotlib inline

Python 3.6.6 :: Anaconda, Inc.


Generation of Questions with a seq2seq network 
*************************************************************

[KEY: > input, = target, < output]

   

This is made possible by the simple but powerful idea of the `sequence
to sequence network <http://arxiv.org/abs/1409.3215>`__, in which two
recurrent neural networks work together to transform one sequence to
another. An encoder network condenses an input sequence into a vector,
and a decoder network unfolds that vector into a new sequence.



To improve upon this model we'll use an `attention
mechanism <https://arxiv.org/abs/1409.0473>`__, which lets the decoder
learn to focus over a specific range of the input sequence.



In [6]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import string
import re
import random

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

Loading data files
===================

The data for this project is a set of many thousands of sentence pairs, broken down into two main groups i.e agreement and no agreement and are present in the dataset folder of the project



Similar to the character encoding used in the character-level RNN
tutorials, we will be representing each word in a language as a one-hot
vector, or giant vector of zeros except for a single one (at the index
of the word). 

We'll need a unique index per word to use as the inputs and targets of
the networks later. To keep track of all this we will use a helper class
called ``Lang`` which has word → index (``word2index``) and index → word
(``index2word``) dictionaries, as well as a count of each word
``word2count`` to use to later replace rare words.




In [9]:
SOS_token = 0
IDENT_TOKEN = -1
QUEST_TOKEN = -1
EOS_TOKEN =1
input_file_path = "./../data/agreement/"
agreement = True

class Lang:
    def __init__(self, name):
        self.name = name
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "SOS", 1: "EOS"}
        self.n_words = 2  # Count SOS and EOS

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1

We shall convert all the words to lower case.

In [10]:
# Converts all to lowercase
def normalizeString(s):
    s = (s.lower().strip())
    return s

To read the data file we will split the file into lines, and then split
lines into pairs




In [11]:
def readLangs(lang1, lang2, reverse=False):
    print("Reading lines...")

    # Read the file and split into lines
    lines = open(input_file_path+'train.txt' ,).\
        read().strip().split('\n')

    # Split every line into pairs and normalize
    pairs = [[normalizeString(s) for s in l.split('\t')] for l in lines]

    # Reverse pairs, make Lang instances
    if reverse:
        pairs = [list(reversed(p)) for p in pairs]
        input_lang = Lang(lang2)
        output_lang = Lang(lang1)
    else:
        input_lang = Lang(lang1)
        output_lang = Lang(lang2)

    return input_lang, output_lang, pairs

The maximum length of each sentence has been set to a 100 words.



In [12]:
MAX_LENGTH = 100
def filterPairs(pairs):
    return [pair for pair in pairs]

The full process for preparing the data is:

-  Read text file and split into lines, split lines into pairs
-  Normalize text, filter by length and content
-  Make word lists from sentences in pairs




In [13]:
def prepareData(lang1, lang2, reverse=False):
    input_lang, output_lang, pairs = readLangs(lang1, lang2, reverse)
    print("Read %s sentence pairs" % len(pairs))
    pairs = filterPairs(pairs)
    print("Trimmed to %s sentence pairs" % len(pairs))
    print("Counting words...")
    for pair in pairs:
        input_lang.addSentence(pair[0])
        output_lang.addSentence(pair[1])
    print("Counted words:")
    print(input_lang.name, input_lang.n_words)
    print(output_lang.name, output_lang.n_words)
    return input_lang, output_lang, pairs


input_lang, output_lang, pairs = prepareData('out', 'inp', True)
IDENT_TOKEN = input_lang.word2index["ident"]
QUEST_TOKEN = input_lang.word2index["quest"]
print(random.choice(pairs))

Reading lines...
Read 116600 sentence pairs
Trimmed to 116600 sentence pairs
Counting words...
Counted words:
inp 55
out 56
['your cat around your rabbits does impress her elephant who doesnt irritate her rabbits . quest', 'does your cat around your rabbits impress her elephant who doesnt irritate her rabbits ? quest']


The Seq2Seq Model
=================

A Recurrent Neural Network, or RNN, is a network that operates on a
sequence and uses its own output as input for subsequent steps.

A `Sequence to Sequence network <http://arxiv.org/abs/1409.3215>`__, or
seq2seq network, or `Encoder Decoder
network <https://arxiv.org/pdf/1406.1078v3.pdf>`__, is a model
consisting of two RNNs called the encoder and decoder. The encoder reads
an input sequence and outputs a single vector, and the decoder reads
that vector to produce an output sequence.


Unlike sequence prediction with a single RNN, where every input
corresponds to an output, the seq2seq model frees us from sequence
length and order, which makes it ideal for translation between two
languages.

With a seq2seq model the encoder creates a single vector which, in the
ideal case, encodes the "meaning" of the input sequence into a single
vector — a single point in some N dimensional space of sentences.

The Encoder
-----------

The encoder of a seq2seq network is a RNN that outputs some value for
every word from the input sentence. For every input word the encoder
outputs a vector and a hidden state, and uses the hidden state for the
next input word.

In [14]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size, hidden_size):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)

    def forward(self, input, hidden):
        embedded = self.embedding(input).view(1, 1, -1)
        output = embedded
        output, hidden = self.gru(output, hidden)
        return output, hidden

    def initHidden(self):
        return torch.randn(1, 1, self.hidden_size, device=device)

The Decoder
-----------

The decoder is another RNN that takes the encoder output vector(s) and
outputs a sequence of words to create the translation.




Simple Decoder
-----------

In the simplest seq2seq decoder we use only last output of the encoder.
This last output is sometimes called the *context vector* as it encodes
context from the entire sequence. This context vector is used as the
initial hidden state of the decoder.

At every step of decoding, the decoder is given an input token and
hidden state. The initial input token is the start-of-string ``<SOS>``
token, and the first hidden state is the context vector (the encoder's
last hidden state).

In [15]:
class DecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size):
        super(DecoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(output_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)
        self.out = nn.Linear(hidden_size, output_size)
        self.softmax = nn.LogSoftmax(dim=1)

    def forward(self, input, hidden):
        output = self.embedding(input).view(1, 1, -1)
        output = F.relu(output)
        output, hidden = self.gru(output, hidden)
        output = self.softmax(self.out(output[0]))
        return output, hidden

    def initHidden(self):
        return torch.randn(1, 1, self.hidden_size, device=device)

Attention Decoder
-----------


If only the context vector is passed betweeen the encoder and decoder,
that single vector carries the burden of encoding the entire sentence.

Attention allows the decoder network to "focus" on a different part of
the encoder's outputs for every step of the decoder's own outputs. First
we calculate a set of *attention weights*. These will be multiplied by
the encoder output vectors to create a weighted combination. The result
(called ``attn_applied`` in the code) should contain information about
that specific part of the input sequence, and thus help the decoder
choose the right output words.


Calculating the attention weights is done with another feed-forward
layer ``attn``, using the decoder's input and hidden state as inputs.
Because there are sentences of all sizes in the training data, to
actually create and train this layer we have to choose a maximum
sentence length (input length, for encoder outputs) that it can apply
to. Sentences of the maximum length will use all the attention weights,
while shorter sentences will only use the first few.

In [16]:
class AttnDecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size, dropout_p=0.1, max_length=MAX_LENGTH):
        super(AttnDecoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.dropout_p = dropout_p
        self.max_length = max_length

        self.embedding = nn.Embedding(self.output_size, self.hidden_size)
        self.attn = nn.Linear(self.hidden_size * 2, self.max_length)
        self.attn_combine = nn.Linear(self.hidden_size * 2, self.hidden_size)
        self.dropout = nn.Dropout(self.dropout_p)
        self.gru = nn.GRU(self.hidden_size, self.hidden_size)
        self.out = nn.Linear(self.hidden_size, self.output_size)

    def forward(self, input, hidden, encoder_outputs):
        embedded = self.embedding(input).view(1, 1, -1)
        embedded = self.dropout(embedded)

        attn_weights = F.softmax(
            self.attn(torch.cat((embedded[0], hidden[0]), 1)), dim=1)
        attn_applied = torch.bmm(attn_weights.unsqueeze(0),
                                 encoder_outputs.unsqueeze(0))

        output = torch.cat((embedded[0], attn_applied[0]), 1)
        output = self.attn_combine(output).unsqueeze(0)

        output = F.relu(output)
        output, hidden = self.gru(output, hidden)

        output = F.log_softmax(self.out(output[0]), dim=1)
        return output, hidden, attn_weights

    def initHidden(self):
        return torch.randn(1, 1, self.hidden_size, device=device)



Training
========

Preparing Training Data
-----------------------

To train, for each pair we will need an input tensor (indexes of the
words in the input sentence) and target tensor (indexes of the words in
the target sentence). While creating these vectors we will append the
EOS token to both sequences.




In [17]:
def indexesFromSentence(lang, sentence):
    return [lang.word2index[word] for word in sentence.split(' ')]


def tensorFromSentence(lang, sentence):
    indexes = indexesFromSentence(lang, sentence)
    if(indexes[-1]!=lang.word2index["ident"] and indexes[-1]!=lang.word2index["quest"]):
        indexes.append(EOS_TOKEN)
        
    return torch.tensor(indexes, dtype=torch.long, device=device).view(-1, 1)


def tensorsFromPair(pair):
    input_tensor = tensorFromSentence(input_lang, pair[0])
    target_tensor = tensorFromSentence(output_lang, pair[1])
    return (input_tensor, target_tensor)

Training the Model
------------------

To train we run the input sentence through the encoder, and keep track
of every output and the latest hidden state. Then the decoder is given
the ``<SOS>`` token as its first input, and the last hidden state of the
encoder as its first hidden state.

"Teacher forcing" is the concept of using the real target outputs as
each next input, instead of using the decoder's guess as the next input.
Using teacher forcing causes it to converge faster but `when the trained
network is exploited, it may exhibit
instability <http://minds.jacobs-university.de/sites/default/files/uploads/papers/ESNTutorialRev.pdf>`__.

You can observe outputs of teacher-forced networks that read with
coherent grammar but wander far from the correct translation -
intuitively it has learned to represent the output grammar and can "pick
up" the meaning once the teacher tells it the first few words, but it
has not properly learned how to create the sentence from the translation
in the first place.

Because of the freedom PyTorch's autograd gives us, we can randomly
choose to use teacher forcing or not with a simple if statement. Turn
``teacher_forcing_ratio`` up to use more of it.




In [18]:
teacher_forcing_ratio = 0.5


def train(input_tensor, target_tensor, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, max_length=MAX_LENGTH):
    encoder_hidden = encoder.initHidden()

    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()

    input_length = input_tensor.size(0)
    target_length = target_tensor.size(0)

    encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

    loss = 0

    for ei in range(input_length):
        encoder_output, encoder_hidden = encoder(
            input_tensor[ei], encoder_hidden)
        encoder_outputs[ei] = encoder_output[0, 0]

    decoder_input = torch.tensor([[SOS_token]], device=device)

    decoder_hidden = encoder_hidden

    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

    if use_teacher_forcing:
        # Teacher forcing: Feed the target as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            loss += criterion(decoder_output, target_tensor[di])
            decoder_input = target_tensor[di]  # Teacher forcing

    else:
        # Without teacher forcing: use its own predictions as the next input
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()  # detach from history as input

            loss += criterion(decoder_output, target_tensor[di])
            if decoder_input.item() == IDENT_TOKEN or decoder_input.item() == QUEST_TOKEN or decoder_input.item()== EOS_TOKEN:
                break

    loss.backward()

    encoder_optimizer.step()
    decoder_optimizer.step()

    return loss.item() / target_length

This is a helper function to print time elapsed and estimated time
remaining given the current time and progress %.




In [19]:
import time
import math


def asMinutes(s):
    m = math.floor(s / 60)
    s -= m * 60
    return '%dm %ds' % (m, s)


def timeSince(since, percent):
    now = time.time()
    s = now - since
    es = s / (percent)
    rs = es - s
    return '%s (- %s)' % (asMinutes(s), asMinutes(rs))

The whole training process looks like this:

-  Start a timer
-  Initialize optimizers and criterion
-  Create set of training pairs
-  Start empty losses array for plotting

Then we call ``train`` many times and occasionally print the progress (%
of examples, time so far, estimated time) and average loss.




In [20]:
def trainIters(encoder, decoder, n_iters, print_every=1000, plot_every=100, learning_rate=0.01):
    start = time.time()
    plot_losses = []
    print_loss_total = 0  # Reset every print_every
    plot_loss_total = 0  # Reset every plot_every

    encoder_optimizer = optim.SGD(encoder.parameters(), lr=learning_rate)
    decoder_optimizer = optim.SGD(decoder.parameters(), lr=learning_rate)
    training_pairs = [tensorsFromPair(random.choice(pairs))
                      for i in range(n_iters)]
    criterion = nn.NLLLoss()

    for iter in range(1, n_iters + 1):
        training_pair = training_pairs[iter - 1]
        input_tensor = training_pair[0]
        target_tensor = training_pair[1]

        loss = train(input_tensor, target_tensor, encoder,
                     decoder, encoder_optimizer, decoder_optimizer, criterion)
        print_loss_total += loss
        plot_loss_total += loss

        if iter % print_every == 0:
            print_loss_avg = print_loss_total / print_every
            print_loss_total = 0
            print('%s (%d %d%%) %.4f' % (timeSince(start, iter / n_iters),
                                         iter, iter / n_iters * 100, print_loss_avg))

        if iter % plot_every == 0:
            plot_loss_avg = plot_loss_total / plot_every
            plot_losses.append(plot_loss_avg)
            plot_loss_total = 0

    showPlot(plot_losses)

Plotting results
----------------

Plotting is done with matplotlib, using the array of loss values
``plot_losses`` saved while training.




In [21]:
import matplotlib.pyplot as plt
plt.switch_backend('agg')
import matplotlib.ticker as ticker
import numpy as np


def showPlot(points):
    plt.figure()
    fig, ax = plt.subplots()
    # this locator puts ticks at regular intervals
    loc = ticker.MultipleLocator(base=0.2)
    ax.yaxis.set_major_locator(loc)
    plt.plot(points)

Evaluation
==========

Evaluation is mostly the same as training, but there are no targets so
we simply feed the decoder's predictions back to itself for each step.
Every time it predicts a word we add it to the output string, and if it
predicts the EOS token we stop there. We also store the decoder's
attention outputs for display later.




In [22]:
def evaluate(encoder, decoder, sentence, max_length=MAX_LENGTH):
    with torch.no_grad():
        input_tensor = tensorFromSentence(input_lang, sentence)
        input_length = input_tensor.size()[0]
        encoder_hidden = encoder.initHidden()

        encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

        for ei in range(input_length):
            encoder_output, encoder_hidden = encoder(input_tensor[ei],
                                                     encoder_hidden)
            encoder_outputs[ei] += encoder_output[0, 0]

        decoder_input = torch.tensor([[SOS_token]], device=device)  # SOS

        decoder_hidden = encoder_hidden

        decoded_words = []
        decoder_attentions = torch.zeros(max_length, max_length)

        for di in range(max_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            decoder_attentions[di] = decoder_attention.data
            topv, topi = decoder_output.data.topk(1)
            if topi.item() == IDENT_TOKEN :
                decoded_words.append('<IDENT>')
                break
            elif topi.item() == QUEST_TOKEN :
                decoded_words.append('<QUEST>')
                break
            elif topi.item() == EOS_TOKEN :
                decoded_words.append('<EOS>')
                break
            else:
                decoded_words.append(output_lang.index2word[topi.item()])

            decoder_input = topi.squeeze().detach()

        return decoded_words, decoder_attentions[:di + 1]

We can evaluate random sentences from the training set and print out the
input, target, and output to make some subjective quality judgements:




In [23]:
def evaluateRandomly(encoder, decoder, n=10):
    for i in range(n):
        pair = random.choice(pairs)
        print('>', pair[0])
        print('=', pair[1])
        output_words, attentions = evaluate(encoder, decoder, pair[0])
        output_sentence = ' '.join(output_words)
        print('<', output_sentence)
        print('')

Training and Evaluating
=======================



In [24]:
class TheModelClass(nn.Module):
    def __init__(self):
        super(TheModelClass, self).__init__()
        self.conv1 = nn.Conv2d(3, 6, 5)
        self.pool = nn.MaxPool2d(2, 2)
        self.conv2 = nn.Conv2d(6, 16, 5)
        self.fc1 = nn.Linear(16 * 5 * 5, 120)
        self.fc2 = nn.Linear(120, 84)
        self.fc3 = nn.Linear(84, 10)

    def forward(self, x):
        x = self.pool(F.relu(self.conv1(x)))
        x = self.pool(F.relu(self.conv2(x)))
        x = x.view(-1, 16 * 5 * 5)
        x = F.relu(self.fc1(x))
        x = F.relu(self.fc2(x))
        x = self.fc3(x)
        return x

# Initialize model
model = TheModelClass()

# Initialize optimizer
optimizer = optim.SGD(model.parameters(), lr=0.001, momentum=0.9)

# Print model's state_dict
print("Model's state_dict:")
for param_tensor in model.state_dict():
    print(param_tensor, "\t", model.state_dict()[param_tensor].size())

# Print optimizer's state_dict
print("Optimizer's state_dict:")
for var_name in optimizer.state_dict():
    print(var_name, "\t", optimizer.state_dict()[var_name])


Model's state_dict:
conv1.weight 	 torch.Size([6, 3, 5, 5])
conv1.bias 	 torch.Size([6])
conv2.weight 	 torch.Size([16, 6, 5, 5])
conv2.bias 	 torch.Size([16])
fc1.weight 	 torch.Size([120, 400])
fc1.bias 	 torch.Size([120])
fc2.weight 	 torch.Size([84, 120])
fc2.bias 	 torch.Size([84])
fc3.weight 	 torch.Size([10, 84])
fc3.bias 	 torch.Size([10])
Optimizer's state_dict:
state 	 {}
param_groups 	 [{'lr': 0.001, 'momentum': 0.9, 'dampening': 0, 'weight_decay': 0, 'nesterov': False, 'params': [4826599784, 4952064576, 4952066448, 4952066376, 4952066520, 4952066592, 4952066664, 4952066736, 4952066808, 4952066880]}]


In [25]:
hidden_size = 256
counter = 3

name = "agreement_"+str(counter)+".pt"
print(name)

encoder1 = EncoderRNN(input_lang.n_words, hidden_size).to(device)
attn_decoder1 = AttnDecoderRNN(hidden_size, output_lang.n_words, dropout_p=0.1).to(device)
trainIters(encoder1, attn_decoder1, 75000, print_every=50)

torch.save(model.state_dict(),name)   
counter+=1
    
  

agreement_3.pt
0m 3s (- 91m 8s) (50 0%) 3.3144
0m 5s (- 69m 31s) (100 0%) 3.0416
0m 7s (- 60m 27s) (150 0%) 3.2065
0m 9s (- 56m 16s) (200 0%) 2.8623
0m 10s (- 53m 19s) (250 0%) 2.7819
0m 12s (- 52m 4s) (300 0%) 2.7887
0m 14s (- 51m 2s) (350 0%) 2.6035
0m 16s (- 50m 42s) (400 0%) 2.6688
0m 18s (- 49m 51s) (450 0%) 2.5003
0m 19s (- 49m 15s) (500 0%) 2.6742
0m 21s (- 48m 52s) (550 0%) 2.5212
0m 23s (- 48m 13s) (600 0%) 2.3689
0m 24s (- 47m 37s) (650 0%) 2.4077
0m 26s (- 47m 23s) (700 0%) 2.3882
0m 28s (- 47m 7s) (750 1%) 2.3714
0m 30s (- 46m 59s) (800 1%) 2.3238
0m 32s (- 46m 58s) (850 1%) 2.4256
0m 34s (- 47m 0s) (900 1%) 2.3406
0m 36s (- 46m 54s) (950 1%) 2.2384
0m 38s (- 46m 53s) (1000 1%) 2.4364
0m 39s (- 46m 46s) (1050 1%) 2.2642
0m 41s (- 46m 36s) (1100 1%) 2.2504
0m 43s (- 46m 28s) (1150 1%) 2.4096
0m 45s (- 46m 24s) (1200 1%) 2.1817
0m 47s (- 46m 28s) (1250 1%) 2.3435
0m 49s (- 46m 34s) (1300 1%) 2.4437
0m 51s (- 46m 26s) (1350 1%) 2.1255
0m 53s (- 46m 26s) (1400 1%) 2.2517
0m 54s

7m 42s (- 43m 0s) (11400 15%) 0.2347
7m 44s (- 42m 58s) (11450 15%) 0.2848
7m 46s (- 42m 57s) (11500 15%) 0.2821
7m 48s (- 42m 56s) (11550 15%) 0.2649
7m 51s (- 42m 55s) (11600 15%) 0.2633
7m 53s (- 42m 54s) (11650 15%) 0.3011
7m 55s (- 42m 53s) (11700 15%) 0.2089
7m 57s (- 42m 52s) (11750 15%) 0.1791
8m 0s (- 42m 51s) (11800 15%) 0.2516
8m 2s (- 42m 50s) (11850 15%) 0.2257
8m 4s (- 42m 48s) (11900 15%) 0.1919
8m 6s (- 42m 48s) (11950 15%) 0.2650
8m 9s (- 42m 47s) (12000 16%) 0.2117
8m 11s (- 42m 47s) (12050 16%) 0.2701
8m 13s (- 42m 46s) (12100 16%) 0.2091
8m 15s (- 42m 45s) (12150 16%) 0.1889
8m 18s (- 42m 43s) (12200 16%) 0.1869
8m 20s (- 42m 42s) (12250 16%) 0.2420
8m 22s (- 42m 41s) (12300 16%) 0.2319
8m 24s (- 42m 39s) (12350 16%) 0.2402
8m 26s (- 42m 38s) (12400 16%) 0.2217
8m 28s (- 42m 36s) (12450 16%) 0.2832
8m 31s (- 42m 35s) (12500 16%) 0.2245
8m 33s (- 42m 33s) (12550 16%) 0.2487
8m 35s (- 42m 33s) (12600 16%) 0.2793
8m 37s (- 42m 31s) (12650 16%) 0.1978
8m 39s (- 42m 30s)

15m 30s (- 37m 7s) (22100 29%) 0.0647
15m 32s (- 37m 5s) (22150 29%) 0.0941
15m 34s (- 37m 3s) (22200 29%) 0.1052
15m 37s (- 37m 1s) (22250 29%) 0.0903
15m 39s (- 36m 59s) (22300 29%) 0.1064
15m 41s (- 36m 57s) (22350 29%) 0.0415
15m 43s (- 36m 55s) (22400 29%) 0.1791
15m 45s (- 36m 53s) (22450 29%) 0.1393
15m 47s (- 36m 51s) (22500 30%) 0.0710
15m 50s (- 36m 49s) (22550 30%) 0.1199
15m 52s (- 36m 47s) (22600 30%) 0.0715
15m 54s (- 36m 45s) (22650 30%) 0.0802
15m 56s (- 36m 44s) (22700 30%) 0.0812
15m 58s (- 36m 42s) (22750 30%) 0.0616
16m 1s (- 36m 40s) (22800 30%) 0.0631
16m 3s (- 36m 38s) (22850 30%) 0.0600
16m 5s (- 36m 36s) (22900 30%) 0.1029
16m 7s (- 36m 34s) (22950 30%) 0.0650
16m 9s (- 36m 32s) (23000 30%) 0.0538
16m 11s (- 36m 29s) (23050 30%) 0.0687
16m 13s (- 36m 27s) (23100 30%) 0.0573
16m 15s (- 36m 25s) (23150 30%) 0.0783
16m 18s (- 36m 23s) (23200 30%) 0.0539
16m 20s (- 36m 21s) (23250 31%) 0.1021
16m 22s (- 36m 19s) (23300 31%) 0.0536
16m 24s (- 36m 17s) (23350 31%) 0.

23m 4s (- 29m 51s) (32700 43%) 0.0154
23m 7s (- 29m 49s) (32750 43%) 0.0263
23m 9s (- 29m 47s) (32800 43%) 0.0194
23m 11s (- 29m 45s) (32850 43%) 0.0344
23m 13s (- 29m 43s) (32900 43%) 0.0308
23m 15s (- 29m 40s) (32950 43%) 0.0181
23m 17s (- 29m 38s) (33000 44%) 0.0289
23m 19s (- 29m 36s) (33050 44%) 0.0255
23m 21s (- 29m 34s) (33100 44%) 0.0255
23m 23s (- 29m 32s) (33150 44%) 0.0193
23m 26s (- 29m 30s) (33200 44%) 0.0335
23m 28s (- 29m 28s) (33250 44%) 0.0250
23m 30s (- 29m 26s) (33300 44%) 0.0232
23m 32s (- 29m 23s) (33350 44%) 0.0147
23m 34s (- 29m 21s) (33400 44%) 0.0160
23m 36s (- 29m 19s) (33450 44%) 0.0230
23m 38s (- 29m 17s) (33500 44%) 0.0221
23m 40s (- 29m 15s) (33550 44%) 0.0255
23m 42s (- 29m 13s) (33600 44%) 0.0218
23m 44s (- 29m 10s) (33650 44%) 0.0378
23m 47s (- 29m 8s) (33700 44%) 0.0203
23m 49s (- 29m 6s) (33750 45%) 0.0283
23m 51s (- 29m 4s) (33800 45%) 0.0285
23m 53s (- 29m 2s) (33850 45%) 0.0245
23m 55s (- 29m 0s) (33900 45%) 0.0237
23m 57s (- 28m 58s) (33950 45%) 0

30m 56s (- 22m 39s) (43300 57%) 0.0080
30m 58s (- 22m 37s) (43350 57%) 0.0087
31m 1s (- 22m 35s) (43400 57%) 0.0142
31m 3s (- 22m 33s) (43450 57%) 0.0103
31m 5s (- 22m 31s) (43500 57%) 0.0090
31m 7s (- 22m 28s) (43550 58%) 0.0154
31m 10s (- 22m 26s) (43600 58%) 0.0076
31m 13s (- 22m 25s) (43650 58%) 0.0069
31m 17s (- 22m 24s) (43700 58%) 0.0104
31m 20s (- 22m 23s) (43750 58%) 0.0163
31m 23s (- 22m 21s) (43800 58%) 0.0079
31m 26s (- 22m 19s) (43850 58%) 0.0098
31m 28s (- 22m 17s) (43900 58%) 0.0070
31m 30s (- 22m 15s) (43950 58%) 0.0078
31m 33s (- 22m 14s) (44000 58%) 0.0084
31m 35s (- 22m 11s) (44050 58%) 0.0125
31m 37s (- 22m 9s) (44100 58%) 0.0064
31m 39s (- 22m 7s) (44150 58%) 0.0071
31m 41s (- 22m 5s) (44200 58%) 0.0066
31m 43s (- 22m 2s) (44250 59%) 0.0061
31m 45s (- 22m 0s) (44300 59%) 0.0913
31m 47s (- 21m 58s) (44350 59%) 0.0110
31m 50s (- 21m 56s) (44400 59%) 0.0094
31m 52s (- 21m 54s) (44450 59%) 0.0079
31m 54s (- 21m 52s) (44500 59%) 0.0147
31m 56s (- 21m 50s) (44550 59%) 0.

38m 52s (- 15m 12s) (53900 71%) 0.0067
38m 54s (- 15m 10s) (53950 71%) 0.0057
38m 57s (- 15m 8s) (54000 72%) 0.0083
38m 59s (- 15m 6s) (54050 72%) 0.0062
39m 1s (- 15m 4s) (54100 72%) 0.0066
39m 3s (- 15m 2s) (54150 72%) 0.0081
39m 6s (- 15m 0s) (54200 72%) 0.0046
39m 8s (- 14m 58s) (54250 72%) 0.0025
39m 10s (- 14m 56s) (54300 72%) 0.0053
39m 12s (- 14m 53s) (54350 72%) 0.0033
39m 14s (- 14m 51s) (54400 72%) 0.0075
39m 17s (- 14m 49s) (54450 72%) 0.0050
39m 19s (- 14m 47s) (54500 72%) 0.0045
39m 21s (- 14m 45s) (54550 72%) 0.0065
39m 23s (- 14m 43s) (54600 72%) 0.0043
39m 26s (- 14m 41s) (54650 72%) 0.0038
39m 28s (- 14m 38s) (54700 72%) 0.0071
39m 30s (- 14m 36s) (54750 73%) 0.0061
39m 33s (- 14m 34s) (54800 73%) 0.0046
39m 35s (- 14m 32s) (54850 73%) 0.0059
39m 37s (- 14m 30s) (54900 73%) 0.0038
39m 39s (- 14m 28s) (54950 73%) 0.0041
39m 41s (- 14m 26s) (55000 73%) 0.0033
39m 44s (- 14m 23s) (55050 73%) 0.0096
39m 46s (- 14m 21s) (55100 73%) 0.0019
39m 48s (- 14m 19s) (55150 73%) 0.

47m 4s (- 7m 34s) (64600 86%) 0.0023
47m 6s (- 7m 32s) (64650 86%) 0.0020
47m 8s (- 7m 30s) (64700 86%) 0.0047
47m 11s (- 7m 28s) (64750 86%) 0.0045
47m 13s (- 7m 26s) (64800 86%) 0.0030
47m 15s (- 7m 23s) (64850 86%) 0.0036
47m 18s (- 7m 21s) (64900 86%) 0.0044
47m 20s (- 7m 19s) (64950 86%) 0.0011
47m 22s (- 7m 17s) (65000 86%) 0.0022
47m 24s (- 7m 15s) (65050 86%) 0.0047
47m 26s (- 7m 12s) (65100 86%) 0.0007
47m 29s (- 7m 10s) (65150 86%) 0.0024
47m 31s (- 7m 8s) (65200 86%) 0.0049
47m 33s (- 7m 6s) (65250 87%) 0.0049
47m 35s (- 7m 4s) (65300 87%) 0.0030
47m 38s (- 7m 2s) (65350 87%) 0.0079
47m 40s (- 6m 59s) (65400 87%) 0.0024
47m 42s (- 6m 57s) (65450 87%) 0.0015
47m 44s (- 6m 55s) (65500 87%) 0.0046
47m 46s (- 6m 53s) (65550 87%) 0.0051
47m 49s (- 6m 51s) (65600 87%) 0.0011
47m 51s (- 6m 48s) (65650 87%) 0.0051
47m 53s (- 6m 46s) (65700 87%) 0.0018
47m 55s (- 6m 44s) (65750 87%) 0.0028
47m 57s (- 6m 42s) (65800 87%) 0.0032
47m 59s (- 6m 40s) (65850 87%) 0.0037
48m 2s (- 6m 37s) (

In [34]:
evaluateRandomly(encoder1, attn_decoder1)

> our rabbit upon our yaks does sleep . ident
= our rabbit upon our yaks does sleep . ident
< our rabbit upon our yaks does sleep . <IDENT>

> our rabbit does entertain my elephants . ident
= our rabbit does entertain my elephants . ident
< our rabbit does entertain my elephants . <IDENT>

> my monkey behind my elephants doesnt irritate some seal with my seal . quest
= doesnt my monkey behind my elephants irritate some seal with my seal ? quest
< doesnt my monkey behind my elephants irritate some seal with my seal <QUEST>

> your rabbit below your seals doesnt confuse your cats below our seals . ident
= your rabbit below your seals doesnt confuse your cats below our seals . ident
< your rabbit below your seals doesnt confuse your cats below our seals . <IDENT>

> our unicorns upon our cat dont sleep . ident
= our unicorns upon our cat dont sleep . ident
< our unicorns upon our cat dont sleep . <IDENT>

> your elephant does impress your elephants that do giggle . quest
= does your eleph

Visualizing Attention
---------------------

A useful property of the attention mechanism is its highly interpretable
outputs. Because it is used to weight specific encoder outputs of the
input sequence, we can imagine looking where the network is focused most
at each time step.

You could simply run ``plt.matshow(attentions)`` to see attention output
displayed as a matrix, with the columns being input steps and rows being
output steps:




In [71]:
output_words, attentions = evaluate(
    encoder1, attn_decoder1, "our cats do read quest")
plt.matshow(attentions.numpy())

KeyError: 'do'

For a better viewing experience we will do the extra work of adding axes
and labels:




In [26]:
def showAttention(input_sentence, output_words, attentions):
    # Set up figure with colorbar
    fig = plt.figure()
    ax = fig.add_subplot(111)
    cax = ax.matshow(attentions.numpy(), cmap='bone')
    fig.colorbar(cax)

    # Set up axes
    ax.set_xticklabels([''] + input_sentence.split(' ') +
                       ['<end>'], rotation=90)
    ax.set_yticklabels([''] + output_words)

    # Show label at every tick
    ax.xaxis.set_major_locator(ticker.MultipleLocator(1))
    ax.yaxis.set_major_locator(ticker.MultipleLocator(1))

    plt.show()
    fig.savefig(input_sentence+'.png')


def evaluateAndShowAttention(input_sentence):
    output_words, attentions = evaluate(
        encoder1, attn_decoder1, input_sentence)
    print('input =', input_sentence)
    print('output =', ' '.join(output_words))
    showAttention(input_sentence, output_words, attentions)


evaluateAndShowAttention("her dog who does smile doesnt confuse your dog who does confuse your unicorn . quest")



input = her dog who does smile doesnt confuse your dog who does confuse your unicorn . quest
output = doesnt her dog who does smile doesnt confuse your dog who does confuse your unicorn <QUEST>


In [27]:
lines = open(input_file_path+'test.txt' ,).\
    read().strip().split('\n')
input_sentences = [] 
output_sentences = []
predicted_sentences = []
failed_full_p = []
failed_full_e = []
failed_pos_p = []
failed_pos_e = []
full_sentence_word_match_counter = 0
full_sentence_pos_match_counter = 0
total_sentences_counter = 0
from eval import *
import string
exclude = set(string.punctuation)

for index in range(len(lines)):
    sentences = lines[index].split("\t")
    normalizedString = (sentences[0].lower()).split(" ")
    #     print(normalizedString)
    normalizedString = list(ch for ch in normalizedString if ch not in exclude)
    #     print(normalizedString)
    input_sent =" ".join(normalizedString)
    #     print(input_sent)
    normalizedString = (sentences[1].lower()).split(" ")
    #     print(normalizedString)
    normalizedString = list(ch for ch in normalizedString if ch not in exclude)
    #     print(normalizedString)
    output_sent =" ".join(normalizedString)
    input_sentences.append(input_sent)
    output_sentences.append(output_sent)
    outwords , out_attn = evaluate(encoder1,attn_decoder1,input_sent,MAX_LENGTH)
    predicted_sentence = " ".join(outwords)
    predicted_sentences.append(predicted_sentence)
    pred = list(ch for ch in outwords if ch not in exclude)
    print(pred)
    if(pred[-1] != "." and pred[-1] != "?"):
        final_pred = pred[:len(pred)-1]
    else:
        final_expected = pred[:len(pred)-1]
    expected = output_sent.split(" ")
    final_expected = expected[:len(expected)-1]
    print(expected)
    print(final_expected)
    print("index" , total_sentences_counter)
    print("Count : pos" , full_sentence_pos_match_counter )
    print ("Count : full" , full_sentence_word_match_counter)
    print(final_pred,final_expected)
    if full_sentence_word_match(final_pred,final_expected):
        full_sentence_word_match_counter+=1
    else:
        failed_full_p.append(final_pred)
        failed_full_e.append(final_expected)
    if full_sentence_pos_match(final_pred,final_expected,agreement):
        full_sentence_pos_match_counter+=1
    else:
        failed_pos_p.append(final_pred)
        failed_pos_e.append(final_expected)
    total_sentences_counter+=1

predictions = open(input_file_path+"predictions_" + str(counter-1) + ".txt","w")
for index in range(total_sentences_counter):
    predictions.write(str(index)+".\n")
    predictions.write("Input:"+input_sentences[index] + "\n")
    predictions.write("Expected Output:" + output_sentences[index]+"\n")
    predictions.write("Predicted:" + predicted_sentences[index] + "\n")
predictions.close()

report = open(input_file_path+"report_" + str(counter-1) + ".txt" , "w")
report.write("Total number Of sentences:" + str(total_sentences_counter) + "\n")
report.write("Total number of correct full sentences word match:" + str(full_sentence_word_match_counter) + "\n")
report.write("Total number of correct full sentences pos match:" + str(full_sentence_pos_match_counter) + "\n")
report.close()

failed = open(input_file_path+"failed_full_"+str(counter-1) + ".txt" , "w")
for index in range(len(failed_full_e)):
    predicted = " ".join(failed_full_p[index])
    expected = " ".join(failed_full_e[index])
    failed.write("Expected:" + expected + " Predicted:" + predicted + "\n")
failed.close()
failed = open(input_file_path+"failed_pos_"+str(counter-1) + ".txt" , "w")
for index in range(len(failed_pos_e)):
    predicted = " ".join(failed_pos_p[index])
    expected = " ".join(failed_pos_e[index])
    failed.write("Expected:" + expected + " Predicted:" + predicted + "\n")
failed.close()

['some', 'cat', 'above', 'some', 'dogs', 'does', 'entertain', 'her', 'dogs', '<IDENT>']
['some', 'cat', 'above', 'some', 'dogs', 'does', 'entertain', 'her', 'dogs', 'ident']
['some', 'cat', 'above', 'some', 'dogs', 'does', 'entertain', 'her', 'dogs']
index 0
Count : pos 0
Count : full 0
['some', 'cat', 'above', 'some', 'dogs', 'does', 'entertain', 'her', 'dogs'] ['some', 'cat', 'above', 'some', 'dogs', 'does', 'entertain', 'her', 'dogs']
['her', 'bird', 'who', 'doesnt', 'live', 'does', 'call', 'our', 'rabbits', 'below', 'our', 'yaks', '<IDENT>']
['her', 'bird', 'who', 'doesnt', 'live', 'does', 'call', 'our', 'rabbits', 'below', 'our', 'yaks', 'ident']
['her', 'bird', 'who', 'doesnt', 'live', 'does', 'call', 'our', 'rabbits', 'below', 'our', 'yaks']
index 1
Count : pos 1
Count : full 1
['her', 'bird', 'who', 'doesnt', 'live', 'does', 'call', 'our', 'rabbits', 'below', 'our', 'yaks'] ['her', 'bird', 'who', 'doesnt', 'live', 'does', 'call', 'our', 'rabbits', 'below', 'our', 'yaks']
['my',

['doesnt', 'my', 'bird', 'call', 'your', 'seals', 'below', 'my', 'seals', '<QUEST>']
['doesnt', 'my', 'bird', 'call', 'your', 'seals', 'below', 'my', 'seals', 'quest']
['doesnt', 'my', 'bird', 'call', 'your', 'seals', 'below', 'my', 'seals']
index 16
Count : pos 16
Count : full 16
['doesnt', 'my', 'bird', 'call', 'your', 'seals', 'below', 'my', 'seals'] ['doesnt', 'my', 'bird', 'call', 'your', 'seals', 'below', 'my', 'seals']
['the', 'yak', 'does', 'confuse', 'the', 'cat', 'behind', 'the', 'yak', '<IDENT>']
['the', 'yak', 'does', 'confuse', 'the', 'cat', 'behind', 'the', 'yak', 'ident']
['the', 'yak', 'does', 'confuse', 'the', 'cat', 'behind', 'the', 'yak']
index 17
Count : pos 17
Count : full 17
['the', 'yak', 'does', 'confuse', 'the', 'cat', 'behind', 'the', 'yak'] ['the', 'yak', 'does', 'confuse', 'the', 'cat', 'behind', 'the', 'yak']
['her', 'elephant', 'who', 'does', 'live', 'does', 'impress', 'our', 'seals', 'who', 'dont', 'impress', 'her', 'elephants', '<IDENT>']
['her', 'elepha

['our', 'cat', 'who', 'doesnt', 'live', 'does', 'irritate', 'our', 'rabbit', 'around', 'the', 'rabbit', '<IDENT>']
['our', 'cat', 'who', 'doesnt', 'live', 'does', 'irritate', 'our', 'rabbit', 'around', 'the', 'rabbit', 'ident']
['our', 'cat', 'who', 'doesnt', 'live', 'does', 'irritate', 'our', 'rabbit', 'around', 'the', 'rabbit']
index 32
Count : pos 32
Count : full 32
['our', 'cat', 'who', 'doesnt', 'live', 'does', 'irritate', 'our', 'rabbit', 'around', 'the', 'rabbit'] ['our', 'cat', 'who', 'doesnt', 'live', 'does', 'irritate', 'our', 'rabbit', 'around', 'the', 'rabbit']
['your', 'dogs', 'that', 'dont', 'confuse', 'your', 'seals', 'do', 'giggle', '<IDENT>']
['your', 'dogs', 'that', 'dont', 'confuse', 'your', 'seals', 'do', 'giggle', 'ident']
['your', 'dogs', 'that', 'dont', 'confuse', 'your', 'seals', 'do', 'giggle']
index 33
Count : pos 33
Count : full 33
['your', 'dogs', 'that', 'dont', 'confuse', 'your', 'seals', 'do', 'giggle'] ['your', 'dogs', 'that', 'dont', 'confuse', 'your', 

['my', 'yak', 'who', 'doesnt', 'smile', 'doesnt', 'impress', 'my', 'yak', 'by', 'my', 'bird', '<IDENT>']
['my', 'yak', 'who', 'doesnt', 'smile', 'doesnt', 'impress', 'my', 'yak', 'by', 'my', 'bird', 'ident']
['my', 'yak', 'who', 'doesnt', 'smile', 'doesnt', 'impress', 'my', 'yak', 'by', 'my', 'bird']
index 47
Count : pos 47
Count : full 47
['my', 'yak', 'who', 'doesnt', 'smile', 'doesnt', 'impress', 'my', 'yak', 'by', 'my', 'bird'] ['my', 'yak', 'who', 'doesnt', 'smile', 'doesnt', 'impress', 'my', 'yak', 'by', 'my', 'bird']
['your', 'rabbit', 'who', 'does', 'smile', 'does', 'call', 'her', 'seal', '<IDENT>']
['your', 'rabbit', 'who', 'does', 'smile', 'does', 'call', 'her', 'seal', 'ident']
['your', 'rabbit', 'who', 'does', 'smile', 'does', 'call', 'her', 'seal']
index 48
Count : pos 48
Count : full 48
['your', 'rabbit', 'who', 'does', 'smile', 'does', 'call', 'her', 'seal'] ['your', 'rabbit', 'who', 'does', 'smile', 'does', 'call', 'her', 'seal']
['your', 'bird', 'behind', 'your', 'rabb

['our', 'yak', 'by', 'our', 'cats', 'does', 'admire', 'my', 'birds', 'that', 'dont', 'irritate', 'our', 'birds', '<IDENT>']
['our', 'yak', 'by', 'our', 'cats', 'does', 'admire', 'my', 'birds', 'that', 'dont', 'irritate', 'our', 'birds', 'ident']
['our', 'yak', 'by', 'our', 'cats', 'does', 'admire', 'my', 'birds', 'that', 'dont', 'irritate', 'our', 'birds']
index 64
Count : pos 64
Count : full 64
['our', 'yak', 'by', 'our', 'cats', 'does', 'admire', 'my', 'birds', 'that', 'dont', 'irritate', 'our', 'birds'] ['our', 'yak', 'by', 'our', 'cats', 'does', 'admire', 'my', 'birds', 'that', 'dont', 'irritate', 'our', 'birds']
['my', 'cat', 'who', 'doesnt', 'confuse', 'our', 'cat', 'does', 'read', '<IDENT>']
['my', 'cat', 'who', 'doesnt', 'confuse', 'our', 'cat', 'does', 'read', 'ident']
['my', 'cat', 'who', 'doesnt', 'confuse', 'our', 'cat', 'does', 'read']
index 65
Count : pos 65
Count : full 65
['my', 'cat', 'who', 'doesnt', 'confuse', 'our', 'cat', 'does', 'read'] ['my', 'cat', 'who', 'doesn

...

['the', 'cat', 'that', 'does', 'irritate', 'her', 'cat', 'doesnt', 'live', '<IDENT>']
['the', 'cat', 'that', 'does', 'irritate', 'her', 'cat', 'doesnt', 'live', 'ident']
['the', 'cat', 'that', 'does', 'irritate', 'her', 'cat', 'doesnt', 'live']
index 8647
Count : pos 8641
Count : full 8551
['the', 'cat', 'that', 'does', 'irritate', 'her', 'cat', 'doesnt', 'live'] ['the', 'cat', 'that', 'does', 'irritate', 'her', 'cat', 'doesnt', 'live']
['your', 'elephant', 'doesnt', 'entertain', 'some', 'elephant', 'upon', 'your', 'yak', '<IDENT>']
['your', 'elephant', 'doesnt', 'entertain', 'some', 'elephant', 'upon', 'your', 'yak', 'ident']
['your', 'elephant', 'doesnt', 'entertain', 'some', 'elephant', 'upon', 'your', 'yak']
index 8648
Count : pos 8642
Count : full 8552
['your', 'elephant', 'doesnt', 'entertain', 'some', 'elephant', 'upon', 'your', 'yak'] ['your', 'elephant', 'doesnt', 'entertain', 'some', 'elephant', 'upon', 'your', 'yak']
['your', 'birds', 'who', 'dont', 'irritate', 'your', 'seal

['our', 'monkeys', 'that', 'dont', 'live', 'do', 'live', '<IDENT>']
['our', 'monkeys', 'that', 'dont', 'live', 'do', 'live', 'ident']
['our', 'monkeys', 'that', 'dont', 'live', 'do', 'live']
index 8670
Count : pos 8664
Count : full 8572
['our', 'monkeys', 'that', 'dont', 'live', 'do', 'live'] ['our', 'monkeys', 'that', 'dont', 'live', 'do', 'live']
['the', 'birds', 'that', 'do', 'sleep', 'dont', 'call', 'the', 'monkey', '<IDENT>']
['the', 'birds', 'that', 'do', 'sleep', 'dont', 'call', 'the', 'monkey', 'ident']
['the', 'birds', 'that', 'do', 'sleep', 'dont', 'call', 'the', 'monkey']
index 8671
Count : pos 8665
Count : full 8573
['the', 'birds', 'that', 'do', 'sleep', 'dont', 'call', 'the', 'monkey'] ['the', 'birds', 'that', 'do', 'sleep', 'dont', 'call', 'the', 'monkey']
['my', 'rabbit', 'upon', 'my', 'seals', 'does', 'admire', 'the', 'elephant', 'who', 'does', 'admire', 'the', 'rabbit', '<IDENT>']
['my', 'rabbit', 'upon', 'my', 'seals', 'does', 'admire', 'the', 'elephant', 'who', 'doe

['the', 'yak', 'doesnt', 'call', 'the', 'monkey', 'by', 'her', 'rabbits', '<IDENT>']
['the', 'yak', 'doesnt', 'call', 'the', 'monkey', 'by', 'her', 'rabbits', 'ident']
['the', 'yak', 'doesnt', 'call', 'the', 'monkey', 'by', 'her', 'rabbits']
index 8690
Count : pos 8684
Count : full 8591
['the', 'yak', 'doesnt', 'call', 'the', 'monkey', 'by', 'her', 'rabbits'] ['the', 'yak', 'doesnt', 'call', 'the', 'monkey', 'by', 'her', 'rabbits']
['my', 'bird', 'near', 'my', 'unicorns', 'doesnt', 'call', 'my', 'elephants', 'who', 'my', 'unicorns', 'dont', 'read', '<IDENT>']
['my', 'bird', 'near', 'my', 'unicorns', 'doesnt', 'call', 'my', 'elephants', 'who', 'my', 'unicorns', 'dont', 'read', 'ident']
['my', 'bird', 'near', 'my', 'unicorns', 'doesnt', 'call', 'my', 'elephants', 'who', 'my', 'unicorns', 'dont', 'read']
index 8691
Count : pos 8685
Count : full 8592
['my', 'bird', 'near', 'my', 'unicorns', 'doesnt', 'call', 'my', 'elephants', 'who', 'my', 'unicorns', 'dont', 'read'] ['my', 'bird', 'near',

['your', 'elephant', 'who', 'doesnt', 'sleep', 'doesnt', 'impress', 'your', 'cats', 'that', 'dont', 'admire', 'your', 'cats', '<IDENT>']
['your', 'elephant', 'who', 'doesnt', 'sleep', 'doesnt', 'impress', 'your', 'cats', 'that', 'dont', 'admire', 'your', 'cats', 'ident']
['your', 'elephant', 'who', 'doesnt', 'sleep', 'doesnt', 'impress', 'your', 'cats', 'that', 'dont', 'admire', 'your', 'cats']
index 8716
Count : pos 8710
Count : full 8617
['your', 'elephant', 'who', 'doesnt', 'sleep', 'doesnt', 'impress', 'your', 'cats', 'that', 'dont', 'admire', 'your', 'cats'] ['your', 'elephant', 'who', 'doesnt', 'sleep', 'doesnt', 'impress', 'your', 'cats', 'that', 'dont', 'admire', 'your', 'cats']
['her', 'dog', 'does', 'impress', 'our', 'elephants', 'with', 'our', 'birds', '<IDENT>']
['her', 'dog', 'does', 'impress', 'our', 'elephants', 'with', 'our', 'birds', 'ident']
['her', 'dog', 'does', 'impress', 'our', 'elephants', 'with', 'our', 'birds']
index 8717
Count : pos 8711
Count : full 8618
['he

['your', 'rabbit', 'by', 'your', 'monkeys', 'does', 'entertain', 'your', 'yaks', 'by', 'your', 'monkeys', '<IDENT>']
['your', 'rabbit', 'by', 'your', 'monkeys', 'does', 'entertain', 'your', 'yaks', 'by', 'your', 'monkeys', 'ident']
['your', 'rabbit', 'by', 'your', 'monkeys', 'does', 'entertain', 'your', 'yaks', 'by', 'your', 'monkeys']
index 8742
Count : pos 8736
Count : full 8643
['your', 'rabbit', 'by', 'your', 'monkeys', 'does', 'entertain', 'your', 'yaks', 'by', 'your', 'monkeys'] ['your', 'rabbit', 'by', 'your', 'monkeys', 'does', 'entertain', 'your', 'yaks', 'by', 'your', 'monkeys']
['your', 'dogs', 'who', 'dont', 'live', 'do', 'impress', 'my', 'dog', '<IDENT>']
['your', 'dogs', 'who', 'dont', 'live', 'do', 'impress', 'my', 'dog', 'ident']
['your', 'dogs', 'who', 'dont', 'live', 'do', 'impress', 'my', 'dog']
index 8743
Count : pos 8737
Count : full 8644
['your', 'dogs', 'who', 'dont', 'live', 'do', 'impress', 'my', 'dog'] ['your', 'dogs', 'who', 'dont', 'live', 'do', 'impress', '

In [28]:
def my_auxiliary_match(prediction, expected):
    '''
        Check if auxiliary matches for generalization set.

        Args:
            prediciton: list of words
            expected: list of words
        Return:
            boolean
    '''
    if prediction[0] == expected[0]:
        return True

    return False
lines = open(input_file_path+'generalisation.txt' ,).\
        read().strip().split('\n')
failed_gen_pos_p = []
failed_gen_full_p = []
failed_gen_pos_e = []
failed_gen_full_e = []
total_lines_gen = 0
full_correct_gen = 0
full_correct_pos = 0
correct_aux = 0
failed_aux_p = []
failed_aux_e  = []
input_sentences=[]
output_sentences = []
predicted_sentences = []
from eval import *
for index in range(len(lines)):
    sentences = lines[index].split("\t")
    normalizedString = (sentences[0].lower()).split(" ")
    #     print(normalizedString)
    normalizedString = list(ch for ch in normalizedString if ch not in exclude)
    #     print(normalizedString)
    input_sent =" ".join(normalizedString)
    #     print(input_sent)
    normalizedString = (sentences[1].lower()).split(" ")
    #     print(normalizedString)
    normalizedString = list(ch for ch in normalizedString if ch not in exclude)
    #     print(normalizedString)
    output_sent =" ".join(normalizedString)
    input_sentences.append(input_sent)
    output_sentences.append(output_sent)
    outwords , out_attn = evaluate(encoder1,attn_decoder1,input_sent,MAX_LENGTH)
    predicted_sentence = " ".join(outwords)
    predicted_sentences.append(predicted_sentence)
    pred = list(ch for ch in outwords if ch not in exclude)
#     print(pred)
    if(pred[-1] != "." and pred[-1] != "?"):
        final_pred = pred[:len(pred)-1]
    else:
        final_expected = pred[:len(pred)-1]
    expected = output_sent.split(" ")
    final_expected = expected[:len(expected)-1]
#     print(expected)
#     print("Final expected " , final_expected)
    print("index" , total_lines_gen)
    print("Count : pos" , full_correct_pos )
    print ("Count : full" , full_correct_gen)
    print("Count : COrrect aux"  ,correct_aux)
    print("Final :" ,  final_pred,final_expected)
    if full_sentence_word_match(final_pred,final_expected):
        full_correct_gen+=1
    else:
        failed_gen_full_p.append(final_pred)
        failed_gen_full_e.append(final_expected)
    if full_sentence_pos_match(final_pred,final_expected,agreement):
        full_correct_pos+=1
    else:
        failed_gen_pos_p.append(final_pred)
        failed_gen_pos_e.append(final_expected)
    if my_auxiliary_match(final_pred , final_expected):
        correct_aux+=1
    else:
        failed_aux_p.append(final_pred)
        failed_aux_e.append(final_expected)

    total_lines_gen+=1

predictions = open(input_file_path+"predictions_gen_" + str(counter-1) + ".txt","w")
for index in range(total_lines_gen):
    predictions.write(str(index)+".\n")
    predictions.write("Input:"+input_sentences[index] + "\n")
    predictions.write("Expected Output:" + output_sentences[index]+"\n")
    predictions.write("Predicted:" + predicted_sentences[index] + "\n")
predictions.close()

report = open(input_file_path+"report_gen_" + str(counter-1) + ".txt" , "w")
report.write("Total number Of sentences:" + str(total_lines_gen) + "\n")
report.write("Total number of correct full sentences word match:" + str(full_correct_gen) + "\n")
report.write("Total number of correct full sentences pos match:" + str(full_correct_pos) + "\n")
report.write("Total number of correct auxillary locations:" + str(correct_aux) + "\n")
report.close()

failed = open(input_file_path+"failed_full_gen_"+str(counter-1) + ".txt" , "w")
for index in range(len(failed_gen_full_p)):
    predicted = " ".join(failed_gen_full_p[index])
    expected = " ".join(failed_gen_full_e[index])
    failed.write("Expected:" + expected + " Predicted:" + predicted + "\n")
failed.close()
failed = open(input_file_path+"failed_pos_gen_"+str(counter-1) + ".txt" , "w")
for index in range(len(failed_gen_pos_p)):
    predicted = " ".join(failed_gen_pos_p[index])
    expected = " ".join(failed_gen_pos_e[index])
    failed.write("Expected:" + expected + " Predicted:" + predicted + "\n")
failed.close()
failed = open(input_file_path+"failed_aux_gen_"+str(counter-1) + ".txt" , "w")
for index in range(len(failed_aux_p)):
    predicted = " ".join(failed_aux_p[index])
    expected = " ".join(failed_aux_e[index])
    failed.write("Expected:" + expected + " Predicted:" + predicted + "\n")
failed.close()





index 0
Count : pos 0
Count : full 0
Count : COrrect aux 0
Final : ['doesnt', 'my', 'seal', 'who', 'the', 'admire', 'the', 'yak', 'does', 'live'] ['does', 'my', 'seal', 'who', 'doesnt', 'admire', 'the', 'yak', 'live']
index 1
Count : pos 0
Count : full 0
Count : COrrect aux 0
Final : ['dont', 'my', 'dogs', 'who', 'dont', 'read', 'do', 'admire', 'my', 'unicorn'] ['do', 'my', 'dogs', 'who', 'dont', 'read', 'admire', 'my', 'unicorn']
index 2
Count : pos 0
Count : full 0
Count : COrrect aux 0
Final : ['does', 'your', 'monkey', 'who', 'laugh', 'doesnt', 'call', 'your', 'dog', 'with', 'our', 'birds'] ['doesnt', 'your', 'monkey', 'who', 'does', 'laugh', 'call', 'your', 'dog', 'with', 'our', 'birds']
index 3
Count : pos 0
Count : full 0
Count : COrrect aux 0
Final : ['doesnt', 'my', 'elephant', 'that', 'the', 'impress', 'the', 'birds'] ['does', 'my', 'elephant', 'that', 'doesnt', 'impress', 'the', 'birds', 'laugh']
index 4
Count : pos 0
Count : full 0
Count : COrrect aux 0
Final : ['do', 'the'

index 34
Count : pos 5
Count : full 0
Count : COrrect aux 6
Final : ['dont', 'the', 'elephants', 'that', 'dont', 'read', 'do', 'call', 'our', 'elephants'] ['do', 'the', 'elephants', 'that', 'dont', 'read', 'call', 'our', 'elephants']
index 35
Count : pos 5
Count : full 0
Count : COrrect aux 6
Final : ['does', 'our', 'elephant', 'who', 'does', 'smile', 'doesnt', 'irritate', 'our', 'unicorn', 'with', 'our', 'elephant'] ['doesnt', 'our', 'elephant', 'who', 'does', 'smile', 'irritate', 'our', 'unicorn', 'with', 'our', 'elephant']
index 36
Count : pos 5
Count : full 0
Count : COrrect aux 6
Final : ['doesnt', 'some', 'rabbit', 'who', 'doesnt', 'sleep', 'does', 'admire', 'some', 'birds'] ['does', 'some', 'rabbit', 'who', 'doesnt', 'sleep', 'admire', 'some', 'birds']
index 37
Count : pos 5
Count : full 0
Count : COrrect aux 6
Final : ['does', 'the', 'yak', 'who', 'laugh', 'doesnt', 'impress', 'her', 'yak', 'upon', 'her', 'monkeys'] ['doesnt', 'the', 'yak', 'who', 'does', 'laugh', 'impress', 'h

index 68
Count : pos 10
Count : full 0
Count : COrrect aux 9
Final : ['doesnt', 'her', 'unicorn', 'who', 'doesnt', 'sleep', 'impress', 'some', 'cat'] ['does', 'her', 'unicorn', 'who', 'doesnt', 'sleep', 'impress', 'some', 'cat']
index 69
Count : pos 11
Count : full 0
Count : COrrect aux 9
Final : ['doesnt', 'my', 'elephant', 'who', 'doesnt', 'live', 'does', 'confuse', 'my', 'rabbit', 'above', 'our', 'elephants'] ['does', 'my', 'elephant', 'who', 'doesnt', 'live', 'confuse', 'my', 'rabbit', 'above', 'our', 'elephants']
index 70
Count : pos 11
Count : full 0
Count : COrrect aux 9
Final : ['doesnt', 'my', 'seal', 'who', 'does', 'live', 'does', 'entertain', 'my', 'cats'] ['does', 'my', 'seal', 'who', 'doesnt', 'live', 'entertain', 'my', 'cats']
index 71
Count : pos 11
Count : full 0
Count : COrrect aux 9
Final : ['doesnt', 'our', 'cat', 'who', 'doesnt', 'giggle', 'admire', 'your', 'elephants', 'by', 'our', 'bird'] ['does', 'our', 'cat', 'who', 'doesnt', 'giggle', 'admire', 'your', 'elephan

index 100
Count : pos 14
Count : full 2
Count : COrrect aux 14
Final : ['doesnt', 'her', 'dog', 'who', 'doesnt', 'giggle', 'does', 'impress', 'my', 'rabbits', 'that', 'my', 'yaks', 'dont', 'giggle'] ['does', 'her', 'dog', 'who', 'doesnt', 'giggle', 'impress', 'my', 'rabbits', 'that', 'my', 'yaks', 'dont', 'smile']
index 101
Count : pos 14
Count : full 2
Count : COrrect aux 14
Final : ['does', 'our', 'rabbit', 'who', 'our', 'admire', 'our', 'rabbit', 'doesnt', 'smile'] ['doesnt', 'our', 'rabbit', 'who', 'does', 'admire', 'our', 'rabbit', 'smile']
index 102
Count : pos 14
Count : full 2
Count : COrrect aux 14
Final : ['doesnt', 'the', 'dog', 'that', 'our', 'elephant', 'does', 'live'] ['does', 'the', 'dog', 'that', 'doesnt', 'irritate', 'our', 'elephant', 'live']
index 103
Count : pos 14
Count : full 2
Count : COrrect aux 14
Final : ['does', 'her', 'monkey', 'who', 'live', 'doesnt', 'admire', 'some', 'yaks', 'by', 'her', 'unicorn'] ['doesnt', 'her', 'monkey', 'who', 'does', 'live', 'admir

index 131
Count : pos 14
Count : full 2
Count : COrrect aux 17
Final : ['does', 'your', 'unicorn', 'that', 'doesnt', 'sleep', 'doesnt', 'entertain', 'her', 'yaks'] ['doesnt', 'your', 'unicorn', 'that', 'does', 'sleep', 'entertain', 'her', 'yaks']
index 132
Count : pos 14
Count : full 2
Count : COrrect aux 17
Final : ['doesnt', 'the', 'dog', 'who', 'doesnt', 'sleep', 'does', 'impress', 'some', 'rabbits', 'who', 'dont', 'sleep'] ['does', 'the', 'dog', 'who', 'doesnt', 'sleep', 'impress', 'some', 'rabbits', 'who', 'dont', 'impress', 'some', 'elephants']
index 133
Count : pos 14
Count : full 2
Count : COrrect aux 17
Final : ['does', 'her', 'cat', 'who', 'does', 'sleep', 'doesnt', 'call', 'her', 'bird', 'behind', 'her', 'dogs'] ['doesnt', 'her', 'cat', 'who', 'does', 'sleep', 'call', 'her', 'bird', 'behind', 'her', 'dogs']
index 134
Count : pos 14
Count : full 2
Count : COrrect aux 17
Final : ['does', 'some', 'yak', 'who', 'read', 'doesnt', 'confuse', 'some', 'rabbits'] ['doesnt', 'some', '

...

index 9843
Count : pos 1024
Count : full 142
Count : COrrect aux 1181
Final : ['doesnt', 'our', 'yak', 'who', 'doesnt', 'smile', 'does', 'call', 'our', 'seal', 'near', 'our', 'seal'] ['does', 'our', 'yak', 'who', 'doesnt', 'smile', 'call', 'our', 'seal', 'near', 'our', 'seal']
index 9844
Count : pos 1024
Count : full 142
Count : COrrect aux 1181
Final : ['doesnt', 'my', 'yak', 'who', 'doesnt', 'live', 'does', 'irritate', 'the', 'cat', 'who', 'doesnt', 'irritate', 'my', 'dogs'] ['does', 'my', 'yak', 'who', 'doesnt', 'live', 'irritate', 'the', 'cat', 'who', 'doesnt', 'irritate', 'my', 'dogs']
index 9845
Count : pos 1024
Count : full 142
Count : COrrect aux 1181
Final : ['doesnt', 'your', 'monkey', 'that', 'the', 'call', 'the', 'seal', 'does', 'giggle'] ['does', 'your', 'monkey', 'that', 'doesnt', 'call', 'the', 'seal', 'giggle']
index 9846
Count : pos 1024
Count : full 142
Count : COrrect aux 1181
Final : ['does', 'her', 'dog', 'who', 'read', 'doesnt', 'irritate', 'her', 'birds', 'behind

index 9878
Count : pos 1026
Count : full 142
Count : COrrect aux 1182
Final : ['does', 'her', 'seal', 'who', 'giggle', 'doesnt', 'irritate', 'our', 'dog', 'by', 'her', 'dog'] ['doesnt', 'her', 'seal', 'who', 'does', 'giggle', 'irritate', 'our', 'dog', 'by', 'her', 'dog']
index 9879
Count : pos 1026
Count : full 142
Count : COrrect aux 1182
Final : ['does', 'our', 'cat', 'who', 'does', 'sleep', 'doesnt', 'call', 'our', 'cat', 'who', 'your', 'elephants', 'do', 'sleep'] ['doesnt', 'our', 'cat', 'who', 'does', 'smile', 'call', 'our', 'cat', 'who', 'your', 'elephants', 'do', 'sleep']
index 9880
Count : pos 1026
Count : full 142
Count : COrrect aux 1182
Final : ['doesnt', 'our', 'cat', 'who', 'dont', 'sleep', 'does', 'impress', 'our', 'monkeys', 'who', 'your', 'monkeys', 'dont', 'giggle'] ['does', 'our', 'cat', 'who', 'doesnt', 'sleep', 'impress', 'our', 'monkeys', 'who', 'your', 'monkeys', 'dont', 'giggle']
index 9881
Count : pos 1026
Count : full 142
Count : COrrect aux 1182
Final : ['does

index 9911
Count : pos 1031
Count : full 144
Count : COrrect aux 1187
Final : ['do', 'some', 'yaks', 'who', 'do', 'live', 'dont', 'live'] ['dont', 'some', 'yaks', 'who', 'do', 'smile', 'live']
index 9912
Count : pos 1031
Count : full 144
Count : COrrect aux 1187
Final : ['does', 'our', 'cat', 'who', 'does', 'smile', 'doesnt', 'call', 'our', 'unicorns', 'who', 'our', 'cats', 'do', 'smile'] ['doesnt', 'our', 'cat', 'who', 'does', 'smile', 'call', 'our', 'unicorns', 'who', 'our', 'cats', 'do', 'smile']
index 9913
Count : pos 1031
Count : full 144
Count : COrrect aux 1187
Final : ['doesnt', 'my', 'yak', 'who', 'doesnt', 'sleep', 'does', 'entertain', 'the', 'monkeys', 'by', 'my', 'unicorns'] ['does', 'my', 'yak', 'who', 'doesnt', 'sleep', 'entertain', 'the', 'monkeys', 'by', 'my', 'unicorns']
index 9914
Count : pos 1031
Count : full 144
Count : COrrect aux 1187
Final : ['doesnt', 'the', 'rabbit', 'who', 'our', 'dog', 'does', 'sleep'] ['does', 'the', 'rabbit', 'who', 'doesnt', 'entertain', '

index 9942
Count : pos 1033
Count : full 144
Count : COrrect aux 1190
Final : ['doesnt', 'your', 'seal', 'who', 'does', 'smile', 'admire', 'your', 'yaks'] ['does', 'your', 'seal', 'who', 'doesnt', 'smile', 'admire', 'your', 'yaks']
index 9943
Count : pos 1034
Count : full 144
Count : COrrect aux 1190
Final : ['doesnt', 'my', 'yak', 'who', 'does', 'giggle', 'confuse', 'our', 'cats', 'who', 'my', 'yak', 'does', 'giggle'] ['doesnt', 'my', 'yak', 'who', 'does', 'giggle', 'confuse', 'our', 'cats', 'who', 'my', 'yak', 'does', 'giggle']
index 9944
Count : pos 1035
Count : full 145
Count : COrrect aux 1191
Final : ['does', 'the', 'yak', 'who', 'live', 'doesnt', 'confuse', 'some', 'rabbits'] ['doesnt', 'the', 'yak', 'who', 'does', 'live', 'confuse', 'some', 'rabbits']
index 9945
Count : pos 1035
Count : full 145
Count : COrrect aux 1191
Final : ['doesnt', 'some', 'monkey', 'who', 'does', 'giggle', 'does', 'admire', 'some', 'unicorn', 'who', 'does', 'admire', 'some', 'elephants'] ['doesnt', 'som

index 9976
Count : pos 1037
Count : full 145
Count : COrrect aux 1192
Final : ['doesnt', 'the', 'elephant', 'who', 'doesnt', 'live', 'does', 'impress', 'some', 'dogs', 'that', 'the', 'monkeys', 'dont', 'read'] ['does', 'the', 'elephant', 'who', 'doesnt', 'live', 'impress', 'some', 'dogs', 'that', 'the', 'monkeys', 'dont', 'read']
index 9977
Count : pos 1037
Count : full 145
Count : COrrect aux 1192
Final : ['dont', 'your', 'elephants', 'who', 'do', 'entertain', 'our', 'elephants', 'dont', 'read'] ['dont', 'your', 'elephants', 'who', 'do', 'entertain', 'our', 'elephants', 'read']
index 9978
Count : pos 1037
Count : full 145
Count : COrrect aux 1193
Final : ['doesnt', 'my', 'bird', 'around', 'the', 'laugh', 'call', 'the', 'dog', 'around', 'my', 'cat'] ['does', 'my', 'bird', 'who', 'doesnt', 'laugh', 'call', 'the', 'dog', 'around', 'my', 'cat']
index 9979
Count : pos 1037
Count : full 145
Count : COrrect aux 1193
Final : ['doesnt', 'the', 'unicorn', 'who', 'does', 'laugh', 'admire', 'the'